### Prueba implementación Saliency y Activation Maps

Visualizamos cómo variaciones en los parámetros del modelo físico
impactan en las unidades del espacio latente.

Para ello comenzamos implementando saliency maps, para entender cómo las variaciones a nivel pixels. 

In [1]:
# Comenzamos generando un modelo y caragando los pesos 
# desde la corrida de SSA

import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras import layers, losses

class ConvAutoencoder(Model):
    
    def __init__(self, latent_dim):
        super().__init__()
        self.latent_dim = latent_dim
        self.encoder = tf.keras.Sequential([layers.InputLayer(input_shape = (30,30,3)), 
                                            layers.Conv2D(8, (5, 5), strides=1, activation = 'relu'),
                                            #layers.MaxPooling2D((2, 2),strides=1, padding = 'same'),
                                            layers.Conv2D(8, (5, 5), strides=1, activation = 'relu'),
                                            #layers.MaxPooling2D((2, 2),strides=1, padding = 'same'),
                                            layers.Conv2D(4, (4, 4), strides=2, activation = 'relu'),
                                            #layers.MaxPooling2D((2, 2),strides=1, padding = 'same'),
                                            layers.Flatten(),
                                            layers.Dense(units = 10*10*4, activation = 'relu'),
                                            #layers.Dense(units = 5*5*4, activation = 'relu'),
                                            layers.Dense(units = 5*5*4, activation = 'relu'),
                                            layers.Dense(latent_dim, activation = 'linear')])
      
        
        self.decoder = tf.keras.Sequential([layers.InputLayer(input_shape=(latent_dim,)),
                                            layers.Dense(units = 5*5*4, activation = 'relu'),
                                            #layers.Dense(units = 5*5*4, activation = 'relu'),
                                            layers.Dense(units = 10*10*4, activation = 'relu'),
                                            
                                            layers.Reshape(target_shape=(10,10,4)),
                                            #layers.UpSampling2D((2, 2)),
                                            layers.Conv2DTranspose(4, (4, 4), strides=2, activation="relu"),
                                            #layers.UpSampling2D((2, 2)),
                                            layers.Conv2DTranspose(8, (5, 5), strides=1, activation="relu"),
                                            layers.Conv2DTranspose(8, (5, 5), strides=1, activation = 'relu'),
                                            layers.Conv2D(3, (4, 4), activation="sigmoid", padding="same")])

    def call(self, X):
        encoded = self.encoder(X)
        decoded = self.decoder(encoded)
        return decoded

2022-04-01 10:22:10.963491: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/jotavecorta/proyectos/mefe2/lib
2022-04-01 10:22:10.963551: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.


In [2]:
import os

# Get weights path
rel_path = os.path.join(os.getcwd(), "../../results")
file_name = "weights_lat_8_ssa_two_layer_ngi.h5"
weights_path = os.path.join(rel_path, file_name)

# Load model with weights
model = ConvAutoencoder(8)
model.build(input_shape=(16000,30,30,3))
model.load_weights(weights_path)

2022-04-01 10:22:17.816710: I tensorflow/stream_executor/cuda/cuda_gpu_executor.cc:923] could not open file to read NUMA node: /sys/bus/pci/devices/0000:01:00.0/numa_node
Your kernel may have been built without NUMA support.
2022-04-01 10:22:17.819535: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/jotavecorta/proyectos/mefe2/lib
2022-04-01 10:22:17.819608: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcublas.so.11'; dlerror: libcublas.so.11: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /home/jotavecorta/proyectos/mefe2/lib
2022-04-01 10:22:17.819652: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcublasLt.so.11'; dlerror: libcublasLt.so.11: cannot open shared object file: No 

Con el modelo entrenado, pasamos imágenes por el encoder y observamos la salida.

In [6]:
from vis.visualization import visualize_activation, visualize_saliency
from vis.utils import utils
# Disable eager to use tf gradients
tf.compat.v1.disable_eager_execution()

# Prepare some input images
file_path = folder = os.getcwd().split('/')[:-2]
file_name = "results/SSA_tl_test_set.pkl"
file_path = os.path.join("/".join(folder), file_name)

import pickle
with open(file_path, "rb") as f:
    sigma_test = pickle.load(f)

# Get layers names and idx
tf.keras.backend.image_data_format()
layer_names = [layer.name for layer in model.encoder.layers]
layer_idx = utils.find_layer_idx(model.encoder, layer_name=layer_names[-1])

# Saliency Maps
seed_input = sigma_test[1, :, :, :]
hetmap = visualize_saliency(model.encoder, layer_idx, 
                            filter_indices=None, seed_input=seed_input)


TypeError: unsupported callable